In [1]:
# @hidden_cell
# The project token is an authorization token that is used to access project resources like data sources, connections, and used by platform APIs.
from project_lib import Project
project = Project(None, project_id='a2826d3f-d5e2-412c-ab71-9eee03b964b6', project_access_token='p-f9cabcce0ae8899714404f43399d9032eb58b9ab')
pc = project.project_context


<img src = "https://pbs.twimg.com/profile_images/971071764913643522/Crczh-as_400x400.jpg" width = 400> </a>

<h1 align=center><font size = 5>Great Divide Brewing: Michigan Expansion Planning</font></h1>

## Introduction

You have been recruited to assist a up and coming Midwestern Microbrewery, Great Divide Brewing, in locating a brewery and taproom in Michigan.<br/>
Great Divide sells well with Household incomes over $75,000 as well as people over 35.<br/>
It offers a lineup of premium Microbrews in styles that range from Bold IPAs to Easy Drinking Pilsners that appeal to more affluent and established professionals.<br/>
Objective is find a city in Michigan that meets these criteria but also has a low density of Breweries.

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

0. <a href="#item0">Install Necessary Libraries</a>
    
1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in New York City</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

## 0. Install Necessary Libraries

Confirm installation of Beadutifulsoup4, HTML Parsers, and related Libraries for creating dataframes, segmenting, clusting, rendering lat/long values, and plotting in maps.

In [2]:
#Confirm installation of Beadutifulsoup4, lxml and html5 html parsers for support of parsing errors in html (lxml is currently most commonly used), and Request Library for fetching websites
!pip install beautifulsoup4
from bs4 import BeautifulSoup

!pip install lxml
!pip install html5

!pip install requests
import requests

In [3]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<a id='item1'></a>

## 1. Download and Explore Datasets

Scrape information from https://en.wikipedia.org/wiki/List_of_Michigan_locations_by_per_capita_income.html

#### Load Michigan per capita income HTML data

In [4]:
!wget -q -O 'List_of_Michigan_locations_by_per_capita_income.html' https://en.wikipedia.org/wiki/List_of_Michigan_locations_by_per_capita_income
print('HTML data downloaded!')

HTML data downloaded!


#### Read Michigan per capita income HTML data into BeautfulSoup
Read HTML into BeautifulSoup and display the formatted source code of the webpage

In [5]:
#Read HTML into BeautifulSoup and prettify to format code indents for readability
with open('List_of_Michigan_locations_by_per_capita_income.html') as html_file:
    soup = BeautifulSoup(html_file, 'lxml')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of Michigan locations by per capita income - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"XpuC8gpAML8AAG3w3qkAAADX","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_Michigan_locations_by_per_capita_income","wgTitle":"List of Michigan locations by per capita income","wgCurRevisionId":951319677,"wgRevisionId":951319677,"wgArticleId":1827915,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles with short description","United States locations by 

#### Find Michigan County Householf Income Table from Soup

Upon examining the Wikipedia Source Code, the Neighborhood information is located in a class of table called 'Wikitable'.
So, set match condition to retreieve Postal Code table.

In [6]:
County_Income_HTML = soup.find('table' , {'class':'wikitable'})
County_Income_HTML

<table class="wikitable sortable">
<tbody><tr valign="bottom">
<th>Rank
</th>
<th>County
</th>
<th>Per capita<br/>income
</th>
<th>Median<br/>household<br/>income
</th>
<th>Median<br/>family<br/>income
</th>
<th>Population
</th>
<th>Number of<br/>households
</th></tr>
<tr>
<td>1
</td>
<td><a href="/wiki/Oakland_County,_Michigan" title="Oakland County, Michigan">Oakland</a>
</td>
<td>$56,138
</td>
<td>$85,991
</td>
<td>$94,783
</td>
<td>1,202,362
</td>
<td>483,698
</td></tr>
<tr>
<td>2
</td>
<td><a href="/wiki/Leelanau_County,_Michigan" title="Leelanau County, Michigan">Leelanau</a>
</td>
<td>$32,194
</td>
<td>$56,527
</td>
<td>$65,342
</td>
<td>21,708
</td>
<td>9,255
</td></tr>
<tr>
<td>3
</td>
<td><a href="/wiki/Livingston_County,_Michigan" title="Livingston County, Michigan">Livingston</a>
</td>
<td>$31,609
</td>
<td>$72,129
</td>
<td>$82,637
</td>
<td>180,967
</td>
<td>67,380
</td></tr>
<tr>
<td>4
</td>
<td><a href="/wiki/Washtenaw_County,_Michigan" title="Washtenaw County, Michigan

#### Read Wikitable data into Pandas Dataframe

In [7]:
table_rows = County_Income_HTML.find_all('tr')

res = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        res.append(row)

County_Income = pd.DataFrame(res, columns=["Rank", "County", "Per Capita Income", "Median Household Income", "Median Family Income", "Population",  "Number of Households" ])
County_Income

Rank          County Per Capita Income Median Household Income  \
0               1         Oakland           $56,138                 $85,991   
1               2        Leelanau           $32,194                 $56,527   
2               3      Livingston           $31,609                 $72,129   
3               4       Washtenaw           $31,316                 $59,065   
4               5      Charlevoix           $28,403                 $48,704   
5               6         Midland           $28,363                 $51,103   
6               7           Emmet           $28,308                 $49,235   
7   United States         $27,334           $51,914                 $62,982   
8               8         Clinton           $27,223                 $58,016   
9               9  Grand Traverse           $27,091                 $50,647   
10             10          Macomb           $26,524                 $53,996   
11             11           Eaton           $25,963                 $54,885   
12             12          Monroe           $25,520                 $55,366   
13             13       Kalamazoo           $25,138                 $44,794   
14       Michigan         $25,135           $48,432                 $60,341   
15             14          Lapeer           $25,110                 $55,005   
16             15          Ottawa           $25,045                 $55,095   
17             16            Kent           $24,791                 $49,532   
18             17           Barry           $24,493                 $51,869   
19             18         Berrien           $24,025                 $42,625   
20             19          Antrim           $23,912                 $43,123   
21             20          Ingham           $23,883                 $45,808   
22             21       Dickinson           $23,854                 $42,586   
23             22       St. Clair           $23,828                 $49,120   
24             23          Benzie           $23,649                 $44,718   
25             24       Marquette           $23,347                 $45,130   
26             25         Allegan           $23,108                 $50,240   
27             26             Bay           $23,049                 $44,659   
28             27       Cheboygan           $23,038                 $37,903   
29             28            Cass           $22,698                 $45,177   
30             29          Otsego           $22,568                 $45,531   
31             30         Lenawee           $22,529                 $48,618   
32             31         Genesee           $22,458                 $43,483   
33             32        Mackinac           $22,170                 $39,339   
34             33         Calhoun           $22,166                 $42,568   
35             34           Wayne           $22,125                 $42,241   
36             35           Huron           $22,098                 $40,038   
37             36           Delta           $22,064                 $41,951   
38             37       Van Buren           $22,002                 $44,435   
39             38         Jackson           $21,947                 $46,117   
40             39      Shiawassee           $21,869                 $46,453   
41             40           Mason           $21,760                 $40,039   
42             41         Saginaw           $21,662                 $42,954   
43             42       Menominee           $21,624                 $41,332   
44             43        Manistee           $21,612                 $40,853   
45             44       Ontonagon           $21,448                 $35,269   
46             45        Keweenaw           $21,307                 $38,872   
47             46          Alpena           $21,140                 $36,695   
48             47        Crawford           $21,002                 $39,665   
49             48         Newaygo           $20,870            

#### Drop Rows that contain erroneous information

The next task is to drop rows where United States or Michigan are shown in table.

In [8]:
County_Income.drop(County_Income[County_Income.Rank.str.contains("i")].index, axis=0, inplace=True, )
County_Income.head()

Rank      County Per Capita Income Median Household Income  \
0    1     Oakland           $56,138                 $85,991   
1    2    Leelanau           $32,194                 $56,527   
2    3  Livingston           $31,609                 $72,129   
3    4   Washtenaw           $31,316                 $59,065   
4    5  Charlevoix           $28,403                 $48,704   

  Median Family Income Population Number of Households  
0              $94,783  1,202,362              483,698  
1              $65,342     21,708                9,255  
2              $82,637    180,967               67,380  
3              $82,184    344,791              137,193  
4              $57,022     25,949               10,882

Sort County_Income alphabetically by county to prepare for merging with age information.

In [9]:
County_Income=County_Income.sort_values('Median Household Income', ascending=False,)
County_Income.reset_index(inplace=True, drop=True)
County_Income.head()

Rank      County Per Capita Income Median Household Income  \
0    1     Oakland           $56,138                 $85,991   
1    3  Livingston           $31,609                 $72,129   
2    4   Washtenaw           $31,316                 $59,065   
3    8     Clinton           $27,223                 $58,016   
4    2    Leelanau           $32,194                 $56,527   

  Median Family Income Population Number of Households  
0              $94,783  1,202,362              483,698  
1              $82,637    180,967               67,380  
2              $82,184    344,791              137,193  
3              $69,611     75,382               28,766  
4              $65,342     21,708                9,255

In [10]:
County_Income.shape

(83, 7)

#### Obtain City Information of Oakland County

Oakland County meets the brewery's income criteria. Let's explore the related cities of Oakland County by scraping List of Municipalities in Michigan page.
https://en.wikipedia.org/wiki/List_of_municipalities_in_Michigan

In [11]:
!wget -q -O 'List_of_municipalities_in_Michigan.html' https://en.wikipedia.org/wiki/List_of_municipalities_in_Michigan
print('HTML data downloaded!')

HTML data downloaded!


In [12]:
#Read HTML into BeautifulSoup and prettify to format code indents for readability
with open('List_of_municipalities_in_Michigan.html') as html_file:
    soup = BeautifulSoup(html_file, 'lxml')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of municipalities in Michigan - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"XpyMjApAMNYAAbXBwa8AAADK","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_municipalities_in_Michigan","wgTitle":"List of municipalities in Michigan","wgCurRevisionId":950285482,"wgRevisionId":950285482,"wgArticleId":236034,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Commons category link is locally defined","Charter townships in Michigan","Cities in Michigan","Lists

In [13]:
mi_cities_HTML = soup.find('table' , {'class':'wikitable'})
#mi_cities_HTML

In [14]:
table_rows = mi_cities_HTML.find_all('tr')

res = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        res.append(row)

mi_cities = pd.DataFrame(res, columns=["Neighborhood", "Type", "County", "Population 2010", "Population 2000", "Change %",  "sq. mi.", "sq. km.", "Density"])
#mi_cities[['Population 2010', 'Population 2000']] = mi_cities[['Population 2010', 'Population 2000']].str.replace(',', '').astype(float) #get rid of commas as they prevent data from being read as numeric
mi_cities['Population 2010'] = mi_cities['Population 2010'].str.replace(',', '').astype(float) #get rid of commas as they prevent data from being read as numeric
mi_cities['Population 2000'] = mi_cities['Population 2000'].str.replace(',', '').astype(float) #get rid of commas as they prevent data from being read as numeric
mi_cities

Neighborhood              Type  \
0                                Acme          Township   
1                                 Ada          Township   
2                               Adams          Township   
3                               Adams          Township   
4                               Adams          Township   
5                             Addison           Village   
6                             Addison          Township   
7                              Adrian              City   
8                              Adrian  Charter Township   
9                               Aetna          Township   
10                              Aetna          Township   
11                             Ahmeek           Village   
12                              Akron           Village   
13                              Akron          Township   
14                          Alabaster          Township   
15                           Alaiedon          Township   
16                              Alamo          Township   
17                            Alanson           Village   
18                              Albee          Township   
19                             Albert          Township   
20                             Albion              City   
21                             Albion          Township   
22                             Alcona          Township   
23                           Algansee          Township   
24                             Algoma          Township   
25                            Algonac              City   
26                            Allegan              City   
27                            Allegan          Township   
28                              Allen           Village   
29                              Allen          Township   
30                          Allendale  Charter Township   
31                         Allen Park              City   
32                              Allis          Township   
33                            Allouez          Township   
34                               Alma              City   
35                             Almena          Township   
36                              Almer          Township   
37                             Almira          Township   
38                             Almont           Village   
39                             Almont          Township   
40                              Aloha          Township   
41                             Alpena              City   
42                             Alpena          Township   
43                              Alpha           Village   
44                             Alpine          Township   
45                              Amber          Township   
46                              Amboy          Township   
47                          Ann Arbor              City   
48                          Ann Arbor  Charter Township   
49                            Antioch          Township   
50                             Antrim          Township   
51                            Antwerp          Township   
52                          Applegate           Village   
53                             Arbela          Township   
54                             Arcada          Township   
55                            Arcadia          Township   
56                            Arcadia          Township   
57                             Arenac          Township   
58                          Argentine          Township   
59                             Argyle          Township   
60                          Arlington          Township   
61                             Armada           Village   
62                             Armada          Township   
63                             Arthur          Township   
64                              Arvon          Township   
65                                Ash          Township   
66                            Ashland          Township   
67           

#### Isolate Cities Related to Oakland County

In [15]:
oakland_cities = mi_cities[mi_cities['County'].isin(['Oakland'])]
oakland_cities.head()

Neighborhood      Type   County  Population 2010  Population 2000  \
6          Addison  Township  Oakland           6351.0           6439.0   
74    Auburn Hills      City  Oakland          21412.0          19837.0   
147        Berkley      City  Oakland          14970.0          15531.0   
159  Beverly Hills   Village  Oakland          10267.0          10437.0   
168  Bingham Farms   Village  Oakland           1111.0           1030.0   

    Change % sq. mi. sq. km.                      Density  
6      −1.4%   35.52    92.0       178.8/sq mi (69.0/km2)  
74     +7.9%    16.6      43    1,289.9/sq mi (498.0/km2)  
147    −3.6%    2.61     6.8  5,735.6/sq mi (2,214.5/km2)  
159    −1.6%    4.00    10.4    2,566.8/sq mi (991.0/km2)  
168    +7.9%    1.21     3.1      918.2/sq mi (354.5/km2)

In [16]:
oakland_cities=oakland_cities.sort_values('Population 2010', ascending=False,)
oakland_cities.reset_index(inplace=True, drop=True)
oakland_cities.head()

Neighborhood              Type   County  Population 2010  \
0              Troy              City  Oakland          80980.0   
1  Farmington Hills              City  Oakland          79740.0   
2        Southfield              City  Oakland          71739.0   
3         Waterford  Charter Township  Oakland          71707.0   
4   Rochester Hills              City  Oakland          70995.0   

   Population 2000 Change % sq. mi. sq. km.                      Density  
0          80959.0     0.0%   33.47    86.7    2,419.5/sq mi (934.2/km2)  
1          82111.0    −2.9%   33.28    86.2    2,396.0/sq mi (925.1/km2)  
2          78296.0    −8.4%   26.27    68.0  2,730.8/sq mi (1,054.4/km2)  
3          73150.0    −2.0%   30.66    79.4    2,338.8/sq mi (903.0/km2)  
4          68825.0    +3.2%   32.82    85.0    2,163.2/sq mi (835.2/km2)

In [17]:
# Remove all columns after 'Population 2010'
oakland_cities.drop(oakland_cities.iloc[:, 4:9], inplace = True, axis = 1) 
#Drop Communities that do not meet the minimum 15,000 people criteria
oakland_cities = oakland_cities[oakland_cities['Population 2010'] > 15000]
oakland_cities

Neighborhood              Type   County  Population 2010
0               Troy              City  Oakland          80980.0
1   Farmington Hills              City  Oakland          79740.0
2         Southfield              City  Oakland          71739.0
3          Waterford  Charter Township  Oakland          71707.0
4    Rochester Hills              City  Oakland          70995.0
5    West Bloomfield  Charter Township  Oakland          64690.0
6            Pontiac              City  Oakland          59515.0
7          Royal Oak              City  Oakland          57236.0
8               Novi              City  Oakland          55224.0
9         Bloomfield  Charter Township  Oakland          41070.0
10          Commerce  Charter Township  Oakland          40186.0
11             Orion  Charter Township  Oakland          35394.0
12      Independence  Charter Township  Oakland          34681.0
13        White Lake  Charter Township  Oakland          30019.0
14   Madison Heights              City  Oakland          29694.0
15          Oak Park              City  Oakland          29319.0
16      Auburn Hills              City  Oakland          21412.0
17            Oxford  Charter Township  Oakland          20526.0
18        Birmingham              City  Oakland          20103.0
19          Ferndale              City  Oakland          19900.0
20          Highland  Charter Township  Oakland          19202.0
21           Oakland  Charter Township  Oakland          16779.0
22        Hazel Park              City  Oakland          16422.0
23           Milford  Charter Township  Oakland          15736.0
24           Brandon  Charter Township  Oakland          15175.0

In [18]:
project.save_data(data=oakland_cities.to_csv(index=False), file_name = 'oakland_cities.csv', overwrite=True)

{'file_name': 'oakland_cities.csv',
 'message': 'File saved to project storage.',
 'bucket_name': 'applieddatasciencecapstonebrewery-donotdelete-pr-aus83pbefagv5w',
 'asset_id': '78ed731e-dd88-4a8c-a01b-d418e8136fe8'}

#### Merge City Latitude, Longitude information

read in latitde and longitude information into dataframe

In [19]:
oakland_cities_latlong=pd.read_csv(project.get_file('oakland_cities_latlon.csv'))
oakland_cities['Latitude'] = oakland_cities_latlong['Latitude'].values
oakland_cities['Longitude'] = oakland_cities_latlong['Longitude'].values
oakland_cities

Neighborhood              Type   County  Population 2010   Latitude  \
0               Troy              City  Oakland          80980.0  42.564000   
1   Farmington Hills              City  Oakland          79740.0  42.485312   
2         Southfield              City  Oakland          71739.0  42.473369   
3          Waterford  Charter Township  Oakland          71707.0  42.702253   
4    Rochester Hills              City  Oakland          70995.0  42.658366   
5    West Bloomfield  Charter Township  Oakland          64690.0  42.569200   
6            Pontiac              City  Oakland          59515.0  42.649199   
7          Royal Oak              City  Oakland          57236.0  42.508646   
8               Novi              City  Oakland          55224.0  42.475590   
9         Bloomfield  Charter Township  Oakland          41070.0  42.575589   
10          Commerce  Charter Township  Oakland          40186.0  42.575866   
11             Orion  Charter Township  Oakland          35394.0  42.751975   
12      Independence  Charter Township  Oakland          34681.0  42.746141   
13        White Lake  Charter Township  Oakland          30019.0  42.654197   
14   Madison Heights              City  Oakland          29694.0  42.503647   
15          Oak Park              City  Oakland          29319.0  42.463091   
16      Auburn Hills              City  Oakland          21412.0  42.674477   
17            Oxford  Charter Township  Oakland          20526.0  42.824752   
18        Birmingham              City  Oakland          20103.0  42.546701   
19          Ferndale              City  Oakland          19900.0  42.460592   
20          Highland  Charter Township  Oakland          19202.0  42.638086   
21           Oakland  Charter Township  Oakland          16779.0  42.756100   
22        Hazel Park              City  Oakland          16422.0  42.462536   
23           Milford  Charter Township  Oakland          15736.0  42.593643   
24           Brandon  Charter Township  Oakland          15175.0  42.848900   

    Longitude  
0  -83.184000  
1  -83.377155  
2  -83.221873  
3  -83.402718  
4  -83.149932  
5  -83.382158  
6  -83.287158  
7  -83.154649  
8  -83.490492  
9  -83.272433  
10 -83.494383  
11 -83.279939  
12 -83.389941  
13 -83.501052  
14 -83.102703  
15 -83.180483  
16 -83.243547  
17 -83.264662  
18 -83.211319  
19 -83.134648  
20 -83.617165  
21 -83.143500  
22 -83.104091  
23 -83.599386  
24 -83.400300

Quickly examine the resulting dataframe.

#### Create a map of Kent County with 10 largest Cities superimposed on top.

In [20]:
address = 'Oakland County, MI'

geolocator = Nominatim(user_agent="mi_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of Oakland County are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Oakland County are 42.6618842, -83.3804439.


In [21]:
# create map of New York using latitude and longitude values

map_oakland = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(oakland_cities['Latitude'], oakland_cities['Longitude'], oakland_cities['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_oakland)    
map_oakland

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the city.

Next, we are going to start utilizing the Foursquare API to explore the Cities and segment them.

In [22]:
oakland_data = oakland_cities[['Neighborhood', 'Latitude', 'Longitude']].reset_index(drop=True) # resets index position of rows
oakland_data.head()

Neighborhood   Latitude  Longitude
0              Troy  42.564000 -83.184000
1  Farmington Hills  42.485312 -83.377155
2        Southfield  42.473369 -83.221873
3         Waterford  42.702253 -83.402718
4   Rochester Hills  42.658366 -83.149932

#### Define Foursquare Credentials and Version

In [23]:
CLIENT_ID = 'AFGXEVNSTEFRFKS3BBBQT1VLN41FMSX5FTQKBFZA5RFOCEUM' # your Foursquare ID
CLIENT_SECRET = '3VPZVIPPZ3T0HQVKRREF5X2WPG34R233ZPGVI45DSLDHGDZD' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: AFGXEVNSTEFRFKS3BBBQT1VLN41FMSX5FTQKBFZA5RFOCEUM
CLIENT_SECRET:3VPZVIPPZ3T0HQVKRREF5X2WPG34R233ZPGVI45DSLDHGDZD


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [24]:
oakland_data.loc[0, 'Neighborhood']

'Troy'

Get the neighborhood's latitude and longitude values.

In [25]:
neighborhood_latitude = oakland_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = oakland_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = oakland_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Troy are 42.56399999999999, -83.184.


#### Now, let's get the top 100 venues that are in Troy within a radius of 1000 meters.

First, let's create the GET request URL. Name your URL **url**.

In [26]:
# type your answer here

LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 1000 # define radius
 # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url



'https://api.foursquare.com/v2/venues/explore?&client_id=AFGXEVNSTEFRFKS3BBBQT1VLN41FMSX5FTQKBFZA5RFOCEUM&client_secret=3VPZVIPPZ3T0HQVKRREF5X2WPG34R233ZPGVI45DSLDHGDZD&v=20180605&ll=42.56399999999999,-83.184&radius=1000&limit=100'

Send the GET request and examine the resutls

In [27]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e9c8c68a2e538001b489b90'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'Downtown Troy',
  'headerFullLocation': 'Downtown Troy, Troy',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 61,
  'suggestedBounds': {'ne': {'lat': 42.573000009000005,
    'lng': -83.17180321282875},
   'sw': {'lat': 42.55499999099998, 'lng': -83.19619678717125}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '41eda300f964a520fe1e1fe3',
       'name': 'The Somerset Collection',
       'location': {'address': '2800 W Big Beaver Rd',
        'crossStreet': 'at Coolidge Hwy',
        'lat': 42.56265279781813,
    

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [28]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [29]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories        lat        lng
0    The Somerset Collection         Shopping Mall  42.562653 -83.183858
1                  Nordstrom         Women's Store  42.562773 -83.185955
2                Chick-fil-A  Fast Food Restaurant  42.562703 -83.183778
3              Louis Vuitton              Boutique  42.562827 -83.184122
4  J. Alexander's Restaurant   American Restaurant  42.562692 -83.184069

And how many venues were returned by Foursquare?

In [30]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

61 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore other Cities with more than 15,000 residents in Oakland County

#### Let's create a function to repeat the same process for remaining cities of interest in Oakland County

In [31]:
def getNearbyVenues(names, latitudes, longitudes, radius=2000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *oakland_venues*.

In [32]:
oakland_venues = getNearbyVenues(names=oakland_data['Neighborhood'],
                                   latitudes=oakland_data['Latitude'],
                                   longitudes=oakland_data['Longitude']
                                  )



Troy
Farmington Hills
Southfield
Waterford
Rochester Hills
West Bloomfield
Pontiac
Royal Oak
Novi
Bloomfield
Commerce
Orion
Independence
White Lake
Madison Heights
Oak Park
Auburn Hills
Oxford
Birmingham
Ferndale
Highland
Oakland
Hazel Park
Milford
Brandon


#### Let's check the size of the resulting dataframe

In [33]:
print(oakland_venues.shape)
oakland_venues

(1339, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                 Troy              42.564000              -83.184000   
1                 Troy              42.564000              -83.184000   
2                 Troy              42.564000              -83.184000   
3                 Troy              42.564000              -83.184000   
4                 Troy              42.564000              -83.184000   
5                 Troy              42.564000              -83.184000   
6                 Troy              42.564000              -83.184000   
7                 Troy              42.564000              -83.184000   
8                 Troy              42.564000              -83.184000   
9                 Troy              42.564000              -83.184000   
10                Troy              42.564000              -83.184000   
11                Troy              42.564000              -83.184000   
12                Troy              42.564000              -83.184000   
13                Troy              42.564000              -83.184000   
14                Troy              42.564000              -83.184000   
15                Troy              42.564000              -83.184000   
16                Troy              42.564000              -83.184000   
17                Troy              42.564000              -83.184000   
18                Troy              42.564000              -83.184000   
19                Troy              42.564000              -83.184000   
20                Troy              42.564000              -83.184000   
21                Troy              42.564000              -83.184000   
22                Troy              42.564000              -83.184000   
23                Troy              42.564000              -83.184000   
24                Troy              42.564000              -83.184000   
25                Troy              42.564000              -83.184000   
26                Troy              42.564000              -83.184000   
27                Troy              42.564000              -83.184000   
28                Troy              42.564000              -83.184000   
29                Troy              42.564000              -83.184000   
30                Troy              42.564000              -83.184000   
31                Troy              42.564000              -83.184000   
32                Troy              42.564000              -83.184000   
33                Troy              42.564000              -83.184000   
34                Troy              42.564000              -83.184000   
35                Troy              42.564000              -83.184000   
36                Troy              42.564000              -83.184000   
37                Troy              42.564000              -83.184000   
38                Troy              42.564000              -83.184000   
39                Troy              42.564000              -83.184000   
40                Troy              42.564000              -83.184000   
41                Troy              42.564000              -83.184000   
42                Troy              42.564000              -83.184000   
43                Troy              42.564000              -83.184000   
44                Troy              42.564000              -83.184000   
45                Troy              42.564000              -83.184000   
46                Troy              42.564000              -83.184000   
47                Troy              42.564000              -83.184000   
48                Troy              42.564000              -83.184000   
49                Troy              42.564000              -83.184000   
50                Troy              42.564000              -83.184000   
51    Farmington Hills              42.485312              -83.377155   
52    Farmington Hills              42.485312              -83.377155   
53    Farmington Hills              42.485312              -83.37715

Let's check how many venues were returned for each neighborhood

In [34]:
oakland_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                             
Auburn Hills                         75                      75     75   
Birmingham                          100                     100    100   
Bloomfield                           19                      19     19   
Brandon                               1                       1      1   
Commerce                             24                      24     24   
Farmington Hills                     32                      32     32   
Ferndale                            100                     100    100   
Hazel Park                           83                      83     83   
Highland                             18                      18     18   
Independence                         41                      41     41   
Madison Heights                     100                     100    100   
Milford                              52                      52     52   
Novi                                100                     100    100   
Oak Park                             76                      76     76   
Oakland                               6                       6      6   
Orion                                16                      16     16   
Oxford                               57                      57     57   
Pontiac                              39                      39     39   
Rochester Hills                      66                      66     66   
Royal Oak                            71                      71     71   
Southfield                           88                      88     88   
Troy                                 51                      51     51   
Waterford                            57                      57     57   
West Bloomfield                      33                      33     33   
White Lake                           34                      34     34   

                  Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                       
Auburn Hills                  75               75              75  
Birmingham                   100              100             100  
Bloomfield                    19               19              19  
Brandon                        1                1               1  
Commerce                      24               24              24  
Farmington Hills              32               32              32  
Ferndale                     100              100             100  
Hazel Park                    83               83              83  
Highland                      18               18              18  
Independence                  41               41              41  
Madison Heights              100              100             100  
Milford                       52               52              52  
Novi                         100              100             100  
Oak Park                      76               76              76  
Oakland                        6                6               6  
Orion                         16               16              16  
Oxford                        57               57              57  
Pontiac                       39               39              39  
Rochester Hills               66               66              66  
Royal Oak                     71               71              71  
Southfield                    88               88              88  
Troy                          51               51              51  
Waterford                     57               57              57  
West Bloomfield               33               33              33  
White Lake                    34               34              34

#### Let's find out how many unique categories can be curated from all the returned venues

In [35]:
print('There are {} uniques categories.'.format(len(oakland_venues['Venue Category'].unique())))

There are 229 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [36]:
# one hot encoding
oakland_onehot = pd.get_dummies(oakland_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
oakland_onehot['Neighborhood'] = oakland_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [oakland_onehot.columns[-1]] + list(oakland_onehot.columns[:-1])                                       
oakland_onehot = oakland_onehot[fixed_columns]
oakland_onehot.head()

Neighborhood  Accessories Store  American Restaurant  Antique Shop  Arcade  \
0         Troy                  0                    0             0       0   
1         Troy                  0                    0             0       0   
2         Troy                  0                    0             0       0   
3         Troy                  0                    0             0       0   
4         Troy                  0                    1             0       0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Australian Restaurant  Auto Garage  Automotive Shop  BBQ Joint  Bagel Shop  \
0                      0            0                0          0           0   
1                      0            0                0          0           0   
2                      0            0                0          0           0   
3                      0            0                0          0           0   
4                      0            0                0          0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Court  Beer Garden  \
0       0     0    0               0                 0            0   
1       0     0    0               0                 0            0   
2       0     0    0               0                 0            0   
3       0     0    0               0                 0            0   
4       0     0    0               0                 0            0   

   Beer Store  Big Box Store  Bike Shop  Bike Trail  Board Shop  \
0           0              0          0           0           0   
1           0              0          0           0           0   
2           0              0          0           0           0   
3           0              0          0           0           0   
4           0              0          0           0           0   

   Boat or Ferry  Bookstore  Boutique  Bowling Alley  Breakfast Spot  Brewery  \
0              0          0         0              0               0        0   
1              0          0         0              0               0        0   
2              0          0         0              0               0        0   
3              0          0         1              0               0        0   
4              0          0         0              0               0        0   

   Bridal Shop  Bubble Tea Shop  Burger Joint  Bus Station  Business Service  \
0            0                0             0            0                 0   
1            0                0             0            0                 0   
2            0                0             0            0                 0   
3            0                0             0            0                 0   
4            0                0             0            0                 0   

   Butcher  Cafeteria  Café  Campground  Chinese Restaurant  Chocolate Shop  \
0        0          0     0           0                   0               0   
1        0          0     0           0                   0               0   
2        0          0     0           0                   0               0   
3        0          0     0           0                   0               0   
4        0          0     0           0                   0               0   

   Clothing Store  Cocktail Bar  Coffee Shop  Comedy Club  Comic Shop  \
0               0             0            0            0           0   
1               0             0            0            0           0   
2               0             0            0            0           0   
3           

And let's examine the new dataframe size.

In [37]:
oakland_onehot.shape

(1339, 230)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [38]:
oakland_grouped = oakland_onehot.groupby('Neighborhood').mean().reset_index()
oakland_grouped

Neighborhood  Accessories Store  American Restaurant  Antique Shop  \
0       Auburn Hills               0.00             0.040000      0.000000   
1         Birmingham               0.00             0.050000      0.000000   
2         Bloomfield               0.00             0.000000      0.000000   
3            Brandon               0.00             0.000000      0.000000   
4           Commerce               0.00             0.000000      0.000000   
5   Farmington Hills               0.00             0.000000      0.000000   
6           Ferndale               0.00             0.000000      0.000000   
7         Hazel Park               0.00             0.012048      0.012048   
8           Highland               0.00             0.055556      0.000000   
9       Independence               0.00             0.024390      0.000000   
10   Madison Heights               0.00             0.040000      0.000000   
11           Milford               0.00             0.057692      0.000000   
12              Novi               0.01             0.020000      0.000000   
13          Oak Park               0.00             0.013158      0.000000   
14           Oakland               0.00             0.000000      0.000000   
15             Orion               0.00             0.000000      0.000000   
16            Oxford               0.00             0.035088      0.000000   
17           Pontiac               0.00             0.000000      0.000000   
18   Rochester Hills               0.00             0.015152      0.000000   
19         Royal Oak               0.00             0.042254      0.000000   
20        Southfield               0.00             0.045455      0.000000   
21              Troy               0.00             0.019608      0.000000   
22         Waterford               0.00             0.070175      0.000000   
23   West Bloomfield               0.00             0.000000      0.000000   
24        White Lake               0.00             0.088235      0.000000   

      Arcade  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0   0.013333    0.000000             0.000000          0.026667   
1   0.000000    0.000000             0.010000          0.000000   
2   0.000000    0.052632             0.000000          0.000000   
3   0.000000    0.000000             0.000000          0.000000   
4   0.000000    0.000000             0.000000          0.000000   
5   0.000000    0.000000             0.031250          0.000000   
6   0.000000    0.000000             0.000000          0.000000   
7   0.000000    0.000000             0.000000          0.000000   
8   0.000000    0.000000             0.000000          0.000000   
9   0.000000    0.000000             0.000000          0.000000   
10  0.000000    0.000000             0.000000          0.010000   
11  0.000000    0.000000             0.000000          0.000000   
12  0.010000    0.000000             0.010000          0.000000   
13  0.000000    0.000000             0.000000          0.000000   
14  0.000000    0.000000             0.000000          0.000000   
15  0.000000    0.000000             0.000000          0.000000   
16  0.000000    0.000000             0.000000          0.000000   
17  0.000000    0.000000             0.000000          0.000000   
18  0.000000    0.000000             0.015152          0.000000   
19  0.000000    0.000000             0.042254          0.000000   
20  0.000000    0.000000             0.000000          0.000000   
21  0.000000    0.000000             0.000000          0.000000   
22  0.000000    0.000000             0.000000          0.000000   
23  0.000000    0.000000             0.000000          0.000000   
24  0.000000    0.000000             0.000000          0.000000   

    Athletics & Sports  Australian Restaurant  Auto Garage  Automotive Shop  \
0             0.000000               0.000000     0.000000         0.000000   
1             0.000000               0.000000     0.000000         0.000000   

#### Let's confirm the new size

In [39]:
oakland_grouped.shape

(25, 230)

#### Let's print each neighborhood along with the top 5 most common venues

In [40]:
num_top_venues = 5

for hood in oakland_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = oakland_grouped[oakland_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Auburn Hills----
                  venue  freq
0        Sandwich Place  0.08
1                 Hotel  0.08
2           Pizza Place  0.07
3  Fast Food Restaurant  0.04
4   American Restaurant  0.04


----Birmingham----
                     venue  freq
0              Coffee Shop  0.05
1      American Restaurant  0.05
2               Steakhouse  0.04
3                      Spa  0.04
4  New American Restaurant  0.03


----Bloomfield----
               venue  freq
0        Pizza Place  0.11
1        Supermarket  0.05
2  Mobile Phone Shop  0.05
3        Fabric Shop  0.05
4        Planetarium  0.05


----Brandon----
               venue  freq
0        Flower Shop   1.0
1  Accessories Store   0.0
2              Motel   0.0
3      Moving Target   0.0
4          Multiplex   0.0


----Commerce----
               venue  freq
0       Liquor Store  0.12
1  Convenience Store  0.12
2               Lake  0.08
3               Park  0.08
4        Pizza Place  0.08


----Farmington Hills----
         

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [41]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [42]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = oakland_grouped['Neighborhood']

for ind in np.arange(oakland_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(oakland_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood   1st Most Common Venue      2nd Most Common Venue  \
0       Auburn Hills          Sandwich Place                      Hotel   
1         Birmingham     American Restaurant                Coffee Shop   
2         Bloomfield             Pizza Place         Frozen Yogurt Shop   
3            Brandon             Flower Shop                Yoga Studio   
4           Commerce       Convenience Store               Liquor Store   
5   Farmington Hills                    Park                      Hotel   
6           Ferndale                     Bar                Coffee Shop   
7         Hazel Park                     Bar                Pizza Place   
8           Highland           Grocery Store                Pizza Place   
9       Independence    Fast Food Restaurant                   Pharmacy   
10   Madison Heights             Coffee Shop       Fast Food Restaurant   
11           Milford          Sandwich Place                Pizza Place   
12              Novi          Sandwich Place     Furniture / Home Store   
13          Oak Park             Pizza Place             Discount Store   
14           Oakland             Golf Course             Farmers Market   
15             Orion                 Dog Run                       Park   
16            Oxford             Pizza Place             Sandwich Place   
17           Pontiac             Pizza Place       Fast Food Restaurant   
18   Rochester Hills  Furniture / Home Store                Yoga Studio   
19         Royal Oak           Grocery Store       Gym / Fitness Center   
20        Southfield                Pharmacy        American Restaurant   
21              Troy      Seafood Restaurant                      Hotel   
22         Waterford     American Restaurant                Pizza Place   
23   West Bloomfield             Golf Course  Middle Eastern Restaurant   
24        White Lake     American Restaurant             Cosmetics Shop   

   3rd Most Common Venue       4th Most Common Venue  \
0            Pizza Place         American Restaurant   
1                    Spa                  Steakhouse   
2             Bagel Shop                    Pharmacy   
3            Gas Station      Furniture / Home Store   
4         Ice Cream Shop                        Lake   
5                   Bank              Sandwich Place   
6         Sandwich Place            Sushi Restaurant   
7         Sandwich Place        Fast Food Restaurant   
8                   Bank          Chinese Restaurant   
9            Pizza Place                Intersection   
10   American Restaurant                 Pizza Place   
11   American Restaurant                 Coffee Shop   
12     Mobile Phone Shop          Mexican Restaurant   
13              Pharmacy              Cosmetics Shop   
14            Restaurant               Garden Center   
15             Gift Shop                    Boutique   
16                  Bank          Chinese Restaurant   
17                 Diner                   Nightclub   
18   Sporting Goods Shop                Intersection   
19   American Restaurant              Sandwich Place   
20        Sandwich Place                Intersection   
21      Department Store                Burger Joint   
22           Gas Station                 Coffee Shop   
23              Pharmacy                       Trail   
24      Department Store  Construction & Landscaping   

         5th Most Common Venue         6th Most Common Venue  \
0                  Coffee Shop          Fast Food Restaurant   
1           Salon / Barbershop                           Gym   
2                  Supermarket  General College & University   
3           Frozen Yogurt Shop           Fried Chicken Joint   
4                         Park                   Pizza Place   
5                      Theater                   Pizza Place   
6                  Pizza Place                  Cocktail Bar   
7                        Diner                          Park   
8            Martial Art

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 3 clusters.

In [50]:
# set number of clusters
kclusters = 5

oakland_grouped_clustering = oakland_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(oakland_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:30] 

array([0, 0, 0, 1, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 3, 0, 0, 0, 0, 0, 0,
       0, 0, 0], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [44]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

oakland_merged = oakland_data

# merge oakland_grouped with oakland_data to add latitude/longitude for each neighborhood
oakland_merged = oakland_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

In [45]:
oakland_merged.head() # check the last columns!

Neighborhood   Latitude  Longitude  Cluster Labels  \
0              Troy  42.564000 -83.184000               0   
1  Farmington Hills  42.485312 -83.377155               0   
2        Southfield  42.473369 -83.221873               0   
3         Waterford  42.702253 -83.402718               0   
4   Rochester Hills  42.658366 -83.149932               0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0      Seafood Restaurant                 Hotel      Department Store   
1                    Park                 Hotel                  Bank   
2                Pharmacy   American Restaurant        Sandwich Place   
3     American Restaurant           Pizza Place           Gas Station   
4  Furniture / Home Store           Yoga Studio   Sporting Goods Shop   

  4th Most Common Venue 5th Most Common Venue   6th Most Common Venue  \
0          Burger Joint    Italian Restaurant  Furniture / Home Store   
1        Sandwich Place               Theater             Pizza Place   
2          Intersection     Mobile Phone Shop      Mexican Restaurant   
3           Coffee Shop   Sporting Goods Shop          Sandwich Place   
4          Intersection  Fast Food Restaurant               Pet Store   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0      Greek Restaurant      Toy / Game Store            Steakhouse   
1                  Café        Shipping Store           Coffee Shop   
2           Coffee Shop           Gas Station         Deli / Bodega   
3    Chinese Restaurant                  Café                 Diner   
4           Coffee Shop      Department Store              Pharmacy   

      10th Most Common Venue  
0          Food & Drink Shop  
1                 Restaurant  
2  Middle Eastern Restaurant  
3       Fast Food Restaurant  
4                       Pool

#### Obtain Neighborhood Latitude, Longitude information

Finally, let's visualize the resulting clusters

In [46]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(oakland_merged['Latitude'], oakland_merged['Longitude'], oakland_merged['Neighborhood'], oakland_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## 5. Examine Clusters

#### Cluster 0
Cluster 0 has a variety of cafe's and restaurants in the top 3 venues.
This would be a good place to look for locating the Brewery, so long as bars and breweries are not common in the Neighborhood.

In [51]:
oakland_merged.loc[oakland_merged['Cluster Labels'] == 0, oakland_merged.columns[[0] + list(range(3, oakland_merged.shape[1]))]]

Neighborhood  Cluster Labels   1st Most Common Venue  \
0               Troy               0      Seafood Restaurant   
1   Farmington Hills               0                    Park   
2         Southfield               0                Pharmacy   
3          Waterford               0     American Restaurant   
4    Rochester Hills               0  Furniture / Home Store   
5    West Bloomfield               0             Golf Course   
6            Pontiac               0             Pizza Place   
7          Royal Oak               0           Grocery Store   
8               Novi               0          Sandwich Place   
9         Bloomfield               0             Pizza Place   
12      Independence               0    Fast Food Restaurant   
13        White Lake               0     American Restaurant   
14   Madison Heights               0             Coffee Shop   
15          Oak Park               0             Pizza Place   
16      Auburn Hills               0          Sandwich Place   
17            Oxford               0             Pizza Place   
18        Birmingham               0     American Restaurant   
19          Ferndale               0                     Bar   
20          Highland               0           Grocery Store   
22        Hazel Park               0                     Bar   
23           Milford               0          Sandwich Place   

        2nd Most Common Venue 3rd Most Common Venue  \
0                       Hotel      Department Store   
1                       Hotel                  Bank   
2         American Restaurant        Sandwich Place   
3                 Pizza Place           Gas Station   
4                 Yoga Studio   Sporting Goods Shop   
5   Middle Eastern Restaurant              Pharmacy   
6        Fast Food Restaurant                 Diner   
7        Gym / Fitness Center   American Restaurant   
8      Furniture / Home Store     Mobile Phone Shop   
9          Frozen Yogurt Shop            Bagel Shop   
12                   Pharmacy           Pizza Place   
13             Cosmetics Shop      Department Store   
14       Fast Food Restaurant   American Restaurant   
15             Discount Store              Pharmacy   
16                      Hotel           Pizza Place   
17             Sandwich Place                  Bank   
18                Coffee Shop                   Spa   
19                Coffee Shop        Sandwich Place   
20                Pizza Place                  Bank   
22                Pizza Place        Sandwich Place   
23                Pizza Place   American Restaurant   

         4th Most Common Venue  5th Most Common Venue  \
0                 Burger Joint     Italian Restaurant   
1               Sandwich Place                Theater   
2                 Intersection      Mobile Phone Shop   
3                  Coffee Shop    Sporting Goods Shop   
4                 Intersection   Fast Food Restaurant   
5                        Trail           Dessert Shop   
6                    Nightclub            Music Venue   
7               Sandwich Place            Pizza Place   
8           Mexican Restaurant            Pizza Place   
9                     Pharmacy            Supermarket   
12                Intersection                    Bar   
13  Construction & Landscaping              Pet Store   
14                 Pizza Place  Vietnamese Restaurant   
15              Cosmetics Shop         Sandwich Place   
16         American Restaurant            Coffee Shop   
17          Chinese Restaurant   Gym / Fitness Center   
18                  Steakhouse     Salon / Barbershop   
19            Sushi Restaurant            Pizza Place   
20          Chinese Restaurant      Martial Arts Dojo   
22        Fast Food Restaurant                  Diner   
23                 Coffee Shop           Burger Joint   

           6th Most Common Venue 7th Most Common Venue  \
0         Furniture / Home Store      Greek Restaurant   
1                

#### Cluster 1
Cluster 1 has appears to be nature and commercial related.
There would probably not be much demand or zoning for a brewery here.

In [52]:
oakland_merged.loc[oakland_merged['Cluster Labels'] == 1, oakland_merged.columns[[0] + list(range(3, oakland_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
24      Brandon               1           Flower Shop           Yoga Studio   

   3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
24           Gas Station  Furniture / Home Store    Frozen Yogurt Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
24   Fried Chicken Joint     French Restaurant      Football Stadium   

   9th Most Common Venue 10th Most Common Venue  
24            Food Truck             Food Court

#### Cluster 2
Cluster 2 has appears to be recreation and industrial related.
There would probably not be much demand or zoning for a brewery here either.

In [53]:
oakland_merged.loc[oakland_merged['Cluster Labels'] == 2, oakland_merged.columns[[0] + list(range(3, oakland_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
21      Oakland               2           Golf Course        Farmers Market   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21            Restaurant         Garden Center     Fish & Chips Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21    Frozen Yogurt Shop   Fried Chicken Joint     French Restaurant   

   9th Most Common Venue 10th Most Common Venue  
21      Football Stadium             Food Truck

#### Cluster 3
Cluster 3 has appears to be recreation and industrial related.
There would probably not be much demand or zoning for a brewery here either.

In [54]:
oakland_merged.loc[oakland_merged['Cluster Labels'] == 3, oakland_merged.columns[[0] + list(range(3, oakland_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
11        Orion               3               Dog Run                  Park   

   3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
11             Gift Shop              Boutique  Construction & Landscaping   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
11          Intersection            Theme Park            Donut Shop   

   9th Most Common Venue 10th Most Common Venue  
11                   Pub             Campground

#### Cluster 4
Cluster 4 has appears to be recreation and industrial related.
There would probably not be much demand or zoning for a brewery here either.

In [55]:
oakland_merged.loc[oakland_merged['Cluster Labels'] == 4, oakland_merged.columns[[0] + list(range(3, oakland_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
10     Commerce               4     Convenience Store          Liquor Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
10        Ice Cream Shop                  Lake                  Park   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
10           Pizza Place             Speakeasy                   Bar   

   9th Most Common Venue 10th Most Common Venue  
10     Electronics Store          Moving Target